# setup 

plan:

1 - make versions of all decent models ive tried (probably about 3 models conv, inception, resnet)

2 - make 3 finetuned nets (vgg16, inceptionv3, resnet50)

3 - train each for 3 folds

4 - combine the features of there models intoa  new model

5 - test that on some data that was held out from thi whole pocess

6 - use that new model which selected features to make preds

note: i dont want to use like 3 different slightly deeper conv models as they are all correlated and probably wont improve ech other very much, so well stick with different conv models, not just ones where i added an extra layer like jun 21-23.


to try next time: leaky relu or parametric relu, https://datascience.stackexchange.com/questions/18583/what-is-the-difference-between-leakyrelu-and-prelu

what i wrote on my todo:

retrain all the models i have so far, instead of 10 folds do 3 for each for more stability, have a holdout set, then do feature stacking with all models to choose the best features (dense or conv?) then use this new stacked model to make preds. should include every model so far. + finetuned vgg, resnet, and inceptionv3, maybe try adding a model with leaky relu, use a bayesian model, try leaky relu.

super helpful posts:

https://mlwave.com/kaggle-ensembling-guide/

https://medium.com/@kuza55/transparent-multi-gpu-training-on-tensorflow-with-keras-8b0016fd9012

https://medium.com/@ManishChablani/https-medium-com-manishchablani-useful-keras-features-4bac0724734c

extras to try next time:

1 - autoencode the iamges to just a few feature maps

2 - use knn to group the images.

3 - see if this model can improve performance

4 - really we want somthing that performs badly (maybe) on everything but better than the rest of the ensemble on the hard to detect set.

note to self:

it is ALWAYS worth checking the structure of your model before training, you may have screwed something up up lik eadding an extra max pool or other. you can just print the layers if a summary is too wordy!

In [1]:
from tensorflow.python.client import device_lib
device_lib.list_local_devices()

[name: "/cpu:0"
 device_type: "CPU"
 memory_limit: 268435456
 locality {
 }
 incarnation: 9793469652000620048, name: "/gpu:0"
 device_type: "GPU"
 memory_limit: 11332668621
 locality {
   bus_id: 1
 }
 incarnation: 4912747096064559908
 physical_device_desc: "device: 0, name: Tesla K80, pci bus id: 0000:04:00.0", name: "/gpu:1"
 device_type: "GPU"
 memory_limit: 11332668621
 locality {
   bus_id: 2
 }
 incarnation: 12124140637621715029
 physical_device_desc: "device: 1, name: Tesla K80, pci bus id: 0000:84:00.0"]

In [2]:
import bcolz
import numpy as np
import pandas as pd
import tensorflow as tf

from scipy import ndimage
from scipy import misc
from scipy.stats import rankdata


import os, gc, sys, glob
from tqdm import tqdm

from sklearn import model_selection
from sklearn import metrics
from sklearn.preprocessing import MinMaxScaler

import keras
from keras import backend as K
from keras import optimizers
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Flatten, Input, Activation, AveragePooling2D, merge
from keras.layers.normalization import BatchNormalization
from keras.metrics import categorical_accuracy
from keras.preprocessing.image import ImageDataGenerator

from keras.layers import Input, GlobalAveragePooling2D, GlobalMaxPooling2D, concatenate
from keras.layers.core import Flatten, Dense, Dropout, Lambda
from keras.layers.convolutional import Convolution2D, MaxPooling2D, ZeroPadding2D

from keras.applications.resnet50 import ResNet50
from keras.applications.inception_v3 import InceptionV3
from keras.applications.vgg16 import VGG16
from keras.applications.vgg19 import VGG19

from keras.callbacks import EarlyStopping, ModelCheckpoint

Using TensorFlow backend.


In [3]:
DATA_DIR = os.path.join('/scratch', 'yns207', 'data_invasive')

path = DATA_DIR
test_path = os.path.join(path, 'test')
models_path = os.path.join(path, 'results')
train_path = os.path.join(path, 'train')
valid_path = os.path.join(path, 'valid')
print('DATA_PATH: ' + path)

DATA_PATH: /scratch/yns207/data_invasive


In [4]:
print('REFRESHING TIMESTAMPS IN: \n')
%cd $DATA_DIR
!touch *
!touch results/*

REFRESHING TIMESTAMPS IN: 

/scratch/yns207/data_invasive


```
%cd $DATA_DIR
!module load centos/7
!7za x '*.7z'
```

# defining funcs

In [5]:
#parallel code from keras extras
#seems to throw some kind of error
#when both are trying to merge back together

from keras.layers import merge
from keras.layers.core import Lambda
from keras.models import Model

import tensorflow as tf

def make_parallel(model, gpu_count):
    def get_slice(data, idx, parts):
        shape = tf.shape(data)
        size = tf.concat([ shape[:1] // parts, shape[1:] ],axis=0)
        stride = tf.concat([ shape[:1] // parts, shape[1:]*0 ],axis=0)
        start = stride * idx
        return tf.slice(data, start, size)

    outputs_all = []
    for i in range(len(model.outputs)):
        outputs_all.append([])

    #Place a copy of the model on each GPU, each getting a slice of the batch
    for i in range(gpu_count):
        with tf.device('/gpu:%d' % i):
            with tf.name_scope('tower_%d' % i) as scope:

                inputs = []
                #Slice each input into a piece for processing on this GPU
                for x in model.inputs:
                    input_shape = tuple(x.get_shape().as_list())[1:]
                    slice_n = Lambda(get_slice, output_shape=input_shape, arguments={'idx':i,'parts':gpu_count})(x)
                    inputs.append(slice_n)                

                outputs = model(inputs)
                
                if not isinstance(outputs, list):
                    outputs = [outputs]
                
                #Save all the outputs for merging back together later
                for l in range(len(outputs)):
                    outputs_all[l].append(outputs[l])

    # merge outputs on CPU
    with tf.device('/cpu:0'):
        merged = []
        for outputs in outputs_all:
            merged.append(merge(outputs, mode='concat', concat_axis=0))
            
        return Model(input=model.inputs, output=merged)

In [6]:
def grab_optimizer(opt, lr):
    if opt == 'sgd':
        return optimizers.SGD(lr=lr, decay=1e-6, momentum=0.8, nesterov=True)
    elif opt == 'adam':
        return optimizers.Adam(lr=lr)
    elif opt == 'adagrad':
        return optimizers.Adagrad(lr=lr)
    elif opt == 'rmsprop':
        return optimizers.RMSprop(lr=lr)

In [7]:
# this is not a naive inception module, it contains many 1x1 convs
# to reduce dimensionality before the 3x3 and 5x5 convs
def inception_block(filter_depth, inputs):
    t1 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu',use_bias=False)(inputs)
    tower_1 = Convolution2D(filter_depth, (3, 3), padding='same', activation='relu', use_bias=False)(t1)
    tower_2 = Convolution2D(filter_depth, (5, 5), padding='same', activation='relu', use_bias=False)(t1)
    tower_3 = AveragePooling2D((3, 3), strides=(1, 1), padding='same')(inputs)
    tower_3 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu', use_bias=False)(tower_3)
    return concatenate([tower_1, tower_2, tower_3], axis=3)

def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

#my attempt at making a resnet identity block, wont be making any conv block
def resnet_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, (1,1), activation=activation)(x)

    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, filter_size, activation=activation, padding='same')(x)
    
    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, (1,1))(x)
    
    shortcut = Convolution2D(filter_depth, (1,1))(inputs)
    shortcut = BatchNormalization()(shortcut)
    
    x = keras.layers.add([x, shortcut])
    x = Activation('relu')(x)
    return x

def make_inception_model(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = BatchNormalization()(inputs)
    m = Convolution2D(16, (3, 3), strides=(2,2), padding='valid', activation='relu')(m)
    m = MaxPooling2D((3, 3), strides=(2, 2))(m)
    m = BatchNormalization()(m)
    m = inception_block(32, m)
    m = inception_block(64, m)
    m = inception_block(128, m)
    m = inception_block(256, m)
    m = GlobalAveragePooling2D()(m)
    m = BatchNormalization()(m)
    m = dense_block(1024, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

def make_resnet_model(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = ZeroPadding2D((3,3))(inputs)
    m = Convolution2D(16, (3,3), strides=(2,2), activation='relu')(m)
    m = MaxPooling2D((3,3), strides=(2,2))(m)
    m = resnet_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = AveragePooling2D((7, 7))(m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

def make_conv_model(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(256, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

def make_finetune_vgg16(input_shape, optimizer):
    base_model = VGG16(input_shape=input_shape, weights='imagenet', include_top=False)
    
    for layer in base_model.layers:
        layer.trainable = False
    
    m = Flatten()(base_model.layers[-1].output)
    m = dense_block(1024, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=base_model.input, outputs=outputs)
    model.compile(loss='binary_crossentropy', 
                  optimizer=optimizer,
                  metrics=['accuracy'])
    return model

def make_finetune_vgg19(input_shape, optimizer):
    base_model = VGG19(input_shape=input_shape, weights='imagenet', include_top=False)
    
    for layer in base_model.layers:
        layer.trainable = False
    
    m = Flatten()(base_model.layers[-1].output)
    m = dense_block(1024, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=base_model.input, outputs=outputs)
    
    model.compile(loss='binary_crossentropy', 
                  optimizer=optimizer,
                  metrics=['accuracy'])
    return model

def make_finetune_resnet50(input_shape, optimizer):
    base_model = ResNet50(input_shape=input_shape, weights='imagenet', include_top=False)

    for layer in base_model.layers:
        layer.trainable = False
    
    m = AveragePooling2D((7, 7))(base_model.layers[-1].output)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)

    model = Model(inputs=base_model.input, outputs=outputs)
    model.compile(loss='binary_crossentropy', 
                  optimizer=optimizer,
                  metrics=['accuracy'])
    return model

def make_finetune_inceptionv3(input_shape, optimizer):
    base_model = InceptionV3(input_shape=input_shape, weights='imagenet', include_top=False)
    
    for layer in base_model.layers:
        layer.trainable = False
    
    m = AveragePooling2D((7, 7))(base_model.layers[-1].output)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)

    model = Model(inputs=base_model.input, outputs=outputs)
    model.compile(loss='binary_crossentropy', 
                  optimizer=optimizer,
                  metrics=['accuracy'])
    return model

# pass on mobile net for now, custom and finetune
def make_mobile_model(input_shape, optimizer):
    pass

def make_finetune_mobilenet(input_shape, optimizer):
    pass

In [8]:
def make_preds(model, test_data):
    # worth leaving a note:
    # prediction 1,2,3 from jun21 had misalgined the test names
    # also submission file 3 and 4 for jun21 are actually both rubmission 4 (accident)
    preds = model.predict(test_data).flatten()
    subm = test_set.copy()
    subm['invasive'] = preds
    return subm

In [9]:
train_set = pd.read_csv(os.path.join(path, 'train_labels.csv'))
test_set = pd.read_csv(os.path.join(path, 'sample_submission.csv'))

In [10]:
train_set.head(2)

name  invasive
0     1         0
1     2         0

In [11]:
#img_shape should eb tuple
#(H,W), height, width
def read_img(img_path, img_shape):
    img = misc.imread(img_path)
    img = misc.imresize(img, img_shape)
    return img

In [12]:
def read_imgs(img_height, img_width):
    train_img, test_img = [],[]
    for img_path in tqdm(train_set['name'].iloc[:]):
        train_img.append(read_img(os.path.join(path, 'train', str(img_path)+'.jpg'), (img_height, img_width)))

    for img_path in tqdm(test_set['name'].iloc[:]):
        test_img.append(read_img(os.path.join(path, 'test', str(img_path)+'.jpg'), (img_height, img_width)))

    train_img = np.array(train_img, np.float32)/255
    test_img = np.array(test_img, np.float32)/255
    train_label = np.array(train_set['invasive'].iloc[:])
    
    return train_img, test_img, train_label

In [13]:
# took out 400x600 because it didnt really
# do much and took up memory
# train_img_300_400, test_img_300_400, train_label_300_400 = read_imgs(300,400)

In [14]:
# create a 10% holdout set of training data to train the stacker model
# cannot make separate for each model because this needs to be used
# to train the stacker model
# train_img, hold_img, train_labels, hold_labels = model_selection.train_test_split(train_img_300_400, train_label_300_400, test_size=0.10)

In [15]:
def save_array(fname, arr):
    c=bcolz.carray(arr, rootdir=fname, mode='w')
    c.flush()

def load_array(fname):
    return bcolz.open(fname)[:]

In [16]:
# %cd $DATA_DIR
# says jul 9 but these were alos used on jul8
# i just hadnt saved them yet
# save_array('jul_9_train_img.dat', train_img)
# save_array('jul_9_hold_img.dat', hold_img)
# save_array('jul_9_train_labels.dat', train_labels)
# save_array('jul_9_hold_labels.dat', hold_labels)

In [17]:
# laod original training/holdout data in case we gotta restart nb
train_img, hold_img = load_array('jul_9_train_img.dat'), load_array('jul_9_hold_img.dat')
train_labels, hold_labels = load_array('jul_9_train_labels.dat'), load_array('jul_9_hold_labels.dat')

In [18]:
print(train_img.shape, hold_img.shape, train_labels.shape, hold_labels.shape)

(2065, 300, 400, 3) (230, 300, 400, 3) (2065,) (230,)


In [19]:
def train_model_k_folds(model, train_data, train_label, model_out,  model_init_weights, epochs, kfolds):
    batch_size = 32
    kf = model_selection.KFold(n_splits=kfolds, shuffle=True)
    score_func = metrics.roc_auc_score

    i = 0
    models_stats = {}
    for train_ixs, valid_ixs in kf.split(train_data):
        x_train = train_data[train_ixs]
        x_valid = train_data[valid_ixs]
        y_train = train_label[train_ixs]
        y_valid = train_label[valid_ixs]

        gen = ImageDataGenerator(
            rotation_range = 30,
            width_shift_range = 0.2,
            height_shift_range = 0.2,
            shear_range = 0.2,
            zoom_range = 0.2,
            horizontal_flip = True,
            vertical_flip = True,
            fill_mode = 'nearest')
        
        #re-initialzie the weights of the model on each run
        model.load_weights(model_init_weights)
        model_out_file = '/scratch/yns207/data_invasive/{}_{}.model'.format(model_out, str(i))
        model_checkpoint = ModelCheckpoint(model_out_file, 
                                            monitor='val_loss', 
                                            save_best_only=True)
        # commenting out early stopping, not gonna use.
#         early_stopping = EarlyStopping(monitor='val_loss', patience=25, verbose=1, mode='auto')

        hist = model.fit_generator(gen.flow(x_train, y_train, batch_size=batch_size),
                            steps_per_epoch=(len(x_train)//batch_size)+1,
                            validation_data=(x_valid,y_valid),
                            validation_steps=(len(x_valid)//batch_size)+1,
                            epochs=epochs,
                            verbose=1,
                            callbacks=[model_checkpoint])
    
        
        
        model.load_weights(model_out_file)
        
        eval_tr = model.evaluate(x_train, y_train)
        eval_va = model.evaluate(x_valid, y_valid)
        
        tr_score = score_func(y_train, model.predict(x_train)[:, 0])
        va_score = score_func(y_valid, model.predict(x_valid)[:, 0])
        
        print('\n')
        print('kfold: {}'.format(str(i)))
        print('best model train acc: {}, loss: {}'.format(eval_tr[1], eval_tr[0]))
        print('best model valid acc: {}, loss: {}'.format(eval_va[1], eval_va[0]))
        print('best model train aroc score: {}, valid aroc score: {}'.format(tr_score, va_score))
        print('\n')
        models_stats[model_out_file] = {'score_tr_va':[tr_score, va_score], 'train_acc_loss':[eval_tr[1], eval_tr[0]], 'val_acc_loss':[eval_va[1], eval_va[0]]}
        
        with open(os.path.join(models_path,'{}_{}.out'.format(model_out,'history')), 'a') as f:
            f.write('kfold: {}'.format(str(i)))
            f.write('best model train acc: {}, loss: {}'.format(eval_tr[1], eval_tr[0]))
            f.write('best model valid acc: {}, loss: {}'.format(eval_va[1], eval_va[0]))
            f.write('best model train aroc score: {}, valid aroc score: {}'.format(tr_score, va_score))
            f.write('\n')
        
        i += 1
    
    return models_stats

In [24]:
def train_model_k_folds_ft(model, train_data, train_label, model_out,  model_init_weights, epochs, kfolds):
    batch_size = 32
    kf = model_selection.KFold(n_splits=kfolds, shuffle=True)
    score_func = metrics.roc_auc_score

    i = 0
    models_stats = {}
    for train_ixs, valid_ixs in kf.split(train_data):
        x_train = train_data[train_ixs]
        x_valid = train_data[valid_ixs]
        y_train = train_label[train_ixs]
        y_valid = train_label[valid_ixs]

        gen = ImageDataGenerator(
            rotation_range = 30,
            width_shift_range = 0.2,
            height_shift_range = 0.2,
            shear_range = 0.2,
            zoom_range = 0.2,
            horizontal_flip = True,
            vertical_flip = True,
            fill_mode = 'nearest')
        
        #re-initialzie the weights of the model on each run
        model.load_weights(model_init_weights)
        model_out_file = '/scratch/yns207/data_invasive/{}_{}.model'.format(model_out, str(i))
        model_checkpoint = ModelCheckpoint(model_out_file, 
                                            monitor='val_loss', 
                                            save_best_only=True)
        # commenting out early stopping, not gonna use.
        # early_stopping = EarlyStopping(monitor='val_loss', patience=25, verbose=1, mode='auto')

        
        print('training dense layers:')
        # fit the dense layers for 1/4 the epochs
        model.fit_generator(gen.flow(x_train, y_train, batch_size=batch_size),
                            steps_per_epoch=(len(x_train)//batch_size)+1,
                            validation_data=(x_valid,y_valid),
                            validation_steps=(len(x_valid)//batch_size)+1,
                            epochs=epochs//4,
                            verbose=1,
                            callbacks=[model_checkpoint])
        print('training last 3 conv layers:')
        # set last conv layer to trainable and fit for 3/4 the epochs
        conv_layers = [layer for layer in model.layers if type(layer) is Convolution2D]
        for layer in conv_layers[-3:]:
            layer.trainable = True

        model.fit_generator(gen.flow(x_train, y_train, batch_size=batch_size),
                            steps_per_epoch=(len(x_train)//batch_size)+1,
                            validation_data=(x_valid,y_valid),
                            validation_steps=(len(x_valid)//batch_size)+1,
                            epochs=epochs-(epochs//4),
                            verbose=1,
                            callbacks=[model_checkpoint])
        
        model.load_weights(model_out_file)
        
        eval_tr = model.evaluate(x_train, y_train)
        eval_va = model.evaluate(x_valid, y_valid)
        
        tr_score = score_func(y_train, model.predict(x_train)[:, 0])
        va_score = score_func(y_valid, model.predict(x_valid)[:, 0])
        
        print('\n')
        print('kfold: {}'.format(str(i)))
        print('best model train acc: {}, loss: {}'.format(eval_tr[1], eval_tr[0]))
        print('best model valid acc: {}, loss: {}'.format(eval_va[1], eval_va[0]))
        print('best model train aroc score: {}, valid aroc score: {}'.format(tr_score, va_score))
        print('\n')
        models_stats[model_out_file] = {'score_tr_va':[tr_score, va_score], 'train_acc_loss':[eval_tr[1], eval_tr[0]], 'val_acc_loss':[eval_va[1], eval_va[0]]}
        
        with open(os.path.join(models_path,'{}_{}.out'.format(model_out,'history')), 'a') as f:
            f.write('kfold: {}'.format(str(i)))
            f.write('best model train acc: {}, loss: {}'.format(eval_tr[1], eval_tr[0]))
            f.write('best model valid acc: {}, loss: {}'.format(eval_va[1], eval_va[0]))
            f.write('best model train aroc score: {}, valid aroc score: {}'.format(tr_score, va_score))
            f.write('\n')
        
        i += 1
    
    return models_stats

# so what's dif this time?

1 - training 7 models

2 - trianing over 5 folds with a 10% holdout

3 - feature stacking/blending preds on the 10% holdout data

4 - use blended stacked model to make preds

5 - use 300x400 for all models, get rid of 128x128

In [ ]:
%cd $DATA_DIR
model_name = 'model_jul8_conv'
conv_model = make_conv_model((300,400,3), grab_optimizer('adam', 0.00025))
conv_model.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(conv_model, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

/scratch/yns207/data_invasive
Epoch 1/100
52/52 [==============================] - 252s - loss: 0.6752 - acc: 0.6960 - val_loss: 2.3567 - val_acc: 0.3632

In [ ]:
%cd $DATA_DIR
model_name = 'model_jul9_resnet'
resnet_model = make_resnet_model((300,400,3), grab_optimizer('adam', 0.00025))
resnet_model.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(resnet_model, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

/scratch/yns207/data_invasive
Epoch 1/100
52/52 [==============================] - 276s - loss: 0.6454 - acc: 0.7152 - val_loss: 1.1024 - val_acc: 0.3729

In [ ]:
%cd $DATA_DIR
model_name = 'model_jul10_inception'
incep_model = make_inception_model((300,400,3), grab_optimizer('adam', 0.00025))
incep_model.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(incep_model, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

/scratch/yns207/data_invasive
Epoch 1/100
52/52 [==============================] - 145s - loss: 0.7120 - acc: 0.6435 - val_loss: 0.6452 - val_acc: 0.6513

In [ ]:
%cd $DATA_DIR
model_name = 'model_jul11_ft_vgg16'
vgg16_ft = make_finetune_vgg16((300,400,3), grab_optimizer('adam', 0.00025))
vgg16_ft.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds_ft(vgg16_ft, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

/scratch/yns207/data_invasive
training dense layers:
Epoch 1/25
52/52 [==============================] - 99s - loss: 0.4994 - acc: 0.7888 - val_loss: 0.7175 - val_acc: 0.6416

In [ ]:
# for next models redirect all output to file.
# also check holdout set has even # of eaxmples before further training!
# write the holdout data to a file so we have it!
# also add multigpu call to make training faster
# make deepest conv layer for finetunes retrained
#do i need to subtract the mean to pass into vgg?
#others didnt seem to in their kernels?

model_name = 'model_jul8_tf_vgg19'
vgg19_ft = make_finetune_vgg19((300,400,3), grab_optimizer('adam', 0.00025))
vgg19_ft.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(vgg19_ft, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

model_name = 'model_jul8_ft_resnet50'
resnet50_ft = make_finetune_resnet50((300,400,3), grab_optimizer('adam', 0.00025))
resnet50_ft.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(resnet50_ft, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

model_name = 'model_jul8_ft_inceptionv3'
incepv3_ft = make_finetune_inceptionv3((300,400,3), grab_optimizer('adam', 0.00025))
incepv3_ft.save_weights('{}_base.model'.format(model_name))
models_stats = train_model_k_folds(incepv3_ft, train_img, train_labels, model_name, '{}_base.model'.format(model_name), 100, 5)

wow these aroc scores suck. i dont even want to submit this. what i will do is just take every single model i have (not just the ones that worked before) and make a rank average prediction. at least then ill have something to submit.

In [ ]:
%cd $DATA_DIR
!touch *
!touch results/*

In [ ]:
_, test_img_22, _ = read_imgs(128,128)
_, test_img_23_24, _ = read_imgs(300,400)
_, test_img_30, _ = read_imgs(400,600)

In [ ]:
# lets try one more ensemble with 3 best conv models, the 3 best resnet models

subm = test_set.iloc[:]
subm = subm.drop('invasive',1)

# 3 best conv models,
# best resnet models, (omitting model 1)
models = [
        'model_jun23_kfold_3.model',
        'model_jun23_kfold_7.model',
        'model_jun23_kfold_9.model',
        'model_jun25_kfold_3.model',
        'model_jun25_kfold_4.model',
        'model_jun25_kfold_5.model',
        'model_jun25_kfold_6.model',
        'model_jun25_kfold_7.model',
        'model_jun30_kfold_0.model',
        'model_jun30_kfold_1.model',
        'model_jun30_kfold_2.model'
        ]

In [ ]:
def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

def make_model_23(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(256, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

def make_model_22(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.55, inputs=m)
    m = dense_block(512, 'relu', 0.65, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

#my attempt at making a resnet identity block, wont be making any conv block
def resnet_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, (1,1), activation=activation)(x)

    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, filter_size, activation=activation, padding='same')(x)
    
    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, (1,1))(x)
    
    shortcut = Convolution2D(filter_depth, (1,1))(inputs)
    shortcut = BatchNormalization()(shortcut)
    
    x = keras.layers.add([x, shortcut])
    x = Activation('relu')(x)
    return x

def make_model_25(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = ZeroPadding2D((3,3))(inputs)
    m = Convolution2D(16, (3,3), strides=(2,2), activation='relu')(m)
    m = MaxPooling2D((3,3), strides=(2,2))(m)
    m = resnet_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = AveragePooling2D((7, 7))(m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# this is not a naive inception module, it contains many 1x1 convs
# to reduce dimensionality before the 3x3 and 5x5 convs
def inception_block(filter_depth, inputs):
    t1 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu',use_bias=False)(inputs)
    tower_1 = Convolution2D(filter_depth, (3, 3), padding='same', activation='relu', use_bias=False)(t1)
    tower_2 = Convolution2D(filter_depth, (5, 5), padding='same', activation='relu', use_bias=False)(t1)
    tower_3 = AveragePooling2D((3, 3), strides=(1, 1), padding='same')(inputs)
    tower_3 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu', use_bias=False)(tower_3)
    return concatenate([tower_1, tower_2, tower_3], axis=3)

def make_model_30(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    
    # convolution preproccesing
    m = BatchNormalization()(inputs)
    m = Convolution2D(16, (3, 3), strides=(2,2), padding='valid', activation='relu')(m)
    m = MaxPooling2D((3, 3), strides=(2, 2))(m)
    #inception blocks
    m = BatchNormalization()(m)
    m = inception_block(32, m)
    m = inception_block(64, m)
    m = inception_block(128, m)
    m = inception_block(256, m)
    m = GlobalAveragePooling2D()(m)
    m = BatchNormalization()(m)
    m = dense_block(1024, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

#omitted 24 because it was just a poorly performing resnet50
model_23 = make_model_23((300,400,3), grab_optimizer('adam', 0.000125))
model_25 = make_model_25((300,400,3), grab_optimizer('adam', 0.0005))
model_30 = make_model_30((400,600,3), grab_optimizer('adam', 0.0005))

for f in models:
    if 'jun23' in f:
        model_23.load_weights(f)
        model_test = model_23
        subm[str(f)] = make_preds(model_test, test_img_23_24)['invasive']
    elif 'jun25' in f:
        model_25.load_weights(f)
        model_test = model_25
        subm[str(f)] = make_preds(model_test, test_img_23_24)['invasive']
    else:
        model_30.load_weights(f)
        model_test = model_30
        subm[str(f)] = make_preds(model_test, test_img_30)['invasive']
subm.head()

In [ ]:
for f in models:
    subm['r_'+str(f)] = rankdata(subm[str(f)])
subm.head()

In [ ]:
subm['r_avg'] = subm[['r_'+f for f in models]].mean(axis=1)
subm.head()

In [ ]:
subm['final_r_blend'] = MinMaxScaler().fit_transform(subm['r_avg'].reshape(-1, 1))

In [ ]:
subm.head()

In [ ]:
subm = subm[['name', 'final_r_blend']]
subm.columns = ['name', 'invasive']
subm.head()

In [ ]:
subm.to_csv(os.path.join(DATA_DIR, 'results', 'subm_jul_2_17_0.gz'), index=False, compression='gzip')

ok WOW. that was a huge improvement. lets just take EVERY model and rank average that shit and see what mo score is. i think the reason this works so well is that different resolutions/models learn different features and so combined become wiser. really what i should be doing is making predictions with each model and storing those, as weights are bigger and to get predictions i have to remake models, idk either way i guess, having the models is kinda nice too.

so we need models for these:

21

22

23

24

25

30

In [ ]:
#jun21 model
#128x128x3
def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = Convolution2D(filter_depth, filter_size, activation=activation)(inputs)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = Dense(units, activation=activation)(inputs)
    x = Dropout(drop_prob)(x)
    return x

def output_block(units, activation, inputs):
    x = Dense(units, activation=activation)(inputs)
    return x

def grab_optimizer(opt, lr):
    if opt == 'sgd':
        return optimizers.SGD(lr=lr, decay=1e-6, momentum=0.8, nesterov=True)
    elif opt == 'adam':
        return optimizers.Adam(lr=lr)
    elif opt == 'adagrad':
        return optimizers.Adagrad(lr=lr)
    elif opt == 'rmsprop':
        return optimizers.RMSprop(lr=lr)

def model_21(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.55, inputs=m)
    m = dense_block(512, 'relu', 0.65, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [ ]:
#jun22 model
#128x128x3
def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

def output_block(units, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    return x

def grab_optimizer(opt, lr):
    if opt == 'sgd':
        return optimizers.SGD(lr=lr, decay=1e-6, momentum=0.8, nesterov=True)
    elif opt == 'adam':
        return optimizers.Adam(lr=lr)
    elif opt == 'adagrad':
        return optimizers.Adagrad(lr=lr)
    elif opt == 'rmsprop':
        return optimizers.RMSprop(lr=lr)

def model_22(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.55, inputs=m)
    m = dense_block(512, 'relu', 0.65, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [ ]:
#jun23 model

# 300x400x3

def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

def output_block(units, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    return x

def grab_optimizer(opt, lr):
    if opt == 'sgd':
        return optimizers.SGD(lr=lr, decay=1e-6, momentum=0.8, nesterov=True)
    elif opt == 'adam':
        return optimizers.Adam(lr=lr)
    elif opt == 'adagrad':
        return optimizers.Adagrad(lr=lr)
    elif opt == 'rmsprop':
        return optimizers.RMSprop(lr=lr)

def model_23(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = conv_block(16, (3,3), (2,2),'relu', inputs=inputs)
    m = conv_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = conv_block(256, (3,3), (2,2), 'relu', inputs=m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [ ]:
#jun24 model

#input 300x400x3

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

def resnet_identity_block(inputs, filters_size, filter_depths):
    x = Convolution2D(filter_depths[0], (1,1))(inputs)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)

    x = Convolution2D(filter_depths[1], filters_size, padding='same')(x)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)

    x = Convolution2D(filter_depths[2], (1,1))(x)
    x = BatchNormalization()(x)

    x = keras.layers.add([x, inputs])
    x = Activation('relu')(x)
    
    return x

def resnet_conv_block(inputs, fitler_size, filter_depths, strides):
    x = Convolution2D(filter_depths[0], (1,1))(inputs)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)
    
    x = Convolution2D(filter_depths[1], fitler_size)(x)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)
    
    x = Convolution2D(filter_depths[2], (1,1))(x)
    x = BatchNormalization()(x)
    
    shortcut = Convolution2D(filter_depths[2], (1,1))(inputs)
    shortcut = BatchNormalization()(shortcut)
    
    x = keras.layers.add([x, shortcut])
    x = Activation('relu')(x)
    
    return x

def model_24(input_shape, optimizer):
    base_model = ResNet50(input_shape=input_shape, weights='imagenet', include_top=False)

    for layer in base_model.layers:
        layer.trainable = False

    m = Flatten()(base_model.layers[-1].output)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)

    model = Model(inputs=base_model.input, outputs=outputs)
    model.compile(loss='binary_crossentropy', 
                  optimizer=optimizer,
                  metrics=['accuracy'])
    return model

In [ ]:
#jun25 model

#input 300x400x3

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

#my attempt at making a resnet identity block, wont be making any conv block
def resnet_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, (1,1), activation=activation)(x)

    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, filter_size, activation=activation, padding='same')(x)
    
    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, (1,1))(x)
    
    shortcut = Convolution2D(filter_depth, (1,1))(inputs)
    shortcut = BatchNormalization()(shortcut)
    
    x = keras.layers.add([x, shortcut])
    x = Activation('relu')(x)
    return x

def model_25(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    m = ZeroPadding2D((3,3))(inputs)
    m = Convolution2D(16, (3,3), strides=(2,2), activation='relu')(m)
    m = MaxPooling2D((3,3), strides=(2,2))(m)
    m = resnet_block(32, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(64, (3,3), (2,2), 'relu', inputs=m)
    m = resnet_block(128, (3,3), (2,2), 'relu', inputs=m)
    m = AveragePooling2D((7, 7))(m)
    m = Flatten()(m)
    m = dense_block(2048, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [ ]:
#jun30 model

#input 400x600x3

def inception_block(filter_depth, inputs):
    t1 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu',use_bias=False)(inputs)
    tower_1 = Convolution2D(filter_depth, (3, 3), padding='same', activation='relu', use_bias=False)(t1)
    tower_2 = Convolution2D(filter_depth, (5, 5), padding='same', activation='relu', use_bias=False)(t1)
    tower_3 = AveragePooling2D((3, 3), strides=(1, 1), padding='same')(inputs)
    tower_3 = Convolution2D(filter_depth, (1, 1), padding='same', activation='relu', use_bias=False)(tower_3)
    return concatenate([tower_1, tower_2, tower_3], axis=3)

def conv_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, filter_size, activation=activation)(x)
    x = MaxPooling2D(pool_size=pool_size)(x)
    return x

def dense_block(units, activation, drop_prob, inputs):
    x = BatchNormalization()(inputs)
    x = Dense(units, activation=activation)(x)
    x = Dropout(drop_prob)(x)
    return x

#my attempt at making a resnet identity block, wont be making any conv block
def resnet_block(filter_depth, filter_size, pool_size, activation, inputs):
    x = BatchNormalization()(inputs)
    x = Convolution2D(filter_depth, (1,1), activation=activation)(x)

    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, filter_size, activation=activation, padding='same')(x)
    
    x = BatchNormalization()(x)
    x = Convolution2D(filter_depth, (1,1))(x)
    
    shortcut = Convolution2D(filter_depth, (1,1))(inputs)
    shortcut = BatchNormalization()(shortcut)
    
    x = keras.layers.add([x, shortcut])
    x = Activation('relu')(x)
    return x

def model_30(input_shape, optimizer):
    inputs = Input(shape=input_shape)
    
    # convolution preproccesing
    m = BatchNormalization()(inputs)
    m = Convolution2D(16, (3, 3), strides=(2,2), padding='valid', activation='relu')(m)
    m = MaxPooling2D((3, 3), strides=(2, 2))(m)
    #inception blocks
    m = BatchNormalization()(m)
    m = inception_block(32, m)
    m = inception_block(64, m)
    m = inception_block(128, m)
    m = inception_block(256, m)
    m = GlobalAveragePooling2D()(m)
    m = BatchNormalization()(m)
    m = dense_block(1024, 'relu', 0.25, inputs=m)
    m = dense_block(512, 'relu', 0.5, inputs=m)
    outputs = dense_block(1, 'sigmoid', 0, inputs=m)
    
    model = Model(inputs=inputs, outputs=outputs)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

In [ ]:
%cd $DATA_DIR

models = glob.glob('*.model')

for f in models:
    print(f)

In [ ]:
#omitted 24 because it was just a poorly performing resnet50
m_model_21 = model_21((128,128,3), grab_optimizer('adam', 0.000125))
m_model_22 = model_22((128,128,3), grab_optimizer('adam', 0.000125))
m_model_23 = model_23((300,400,3), grab_optimizer('adam', 0.000125))
m_model_24 = model_24((300,400,3), grab_optimizer('adam', 0.0005))
m_model_25 = model_25((300,400,3), grab_optimizer('adam', 0.0005))
m_model_30 = model_30((400,600,3), grab_optimizer('adam', 0.0005))

subm = test_set.iloc[:]
subm = subm.drop('invasive',1)

In [ ]:
_, imgs_128_128, _ = read_imgs(128,128)
_, imgs_300_400, _ = read_imgs(300,400)
_, imgs_400_600, _ = read_imgs(400,600)

In [ ]:
for f in models:
    print(f)
    try:
        if 'jun21' in f and not 'base' in f:
            m_model_21.load_weights(f)
            subm[str(f)] = make_preds(m_model_21, imgs_128_128)['invasive']
        elif 'jun22' in f and not 'base' in f:
            m_model_22.load_weights(f)
            subm[str(f)] = make_preds(m_model_22, imgs_128_128)['invasive']
        elif 'jun23' in f and not 'base' in f:
            m_model_23.load_weights(f)
            subm[str(f)] = make_preds(m_model_23, imgs_300_400)['invasive']
        elif 'jun24' in f and not 'base' in f:
            m_model_24.load_weights(f)
            subm[str(f)] = make_preds(m_model_24, imgs_300_400)['invasive']      
        elif 'jun25' in f and not 'base' in f:
            m_model_25.load_weights(f)
            subm[str(f)] = make_preds(m_model_25, imgs_300_400)['invasive']
        else:
            m_model_30.load_weights(f)
            subm[str(f)] = make_preds(m_model_30, imgs_400_600)['invasive']
    except ValueError as e:
        print(e)
subm.head()

In [ ]:
for f in models:
    if f in subm.columns:
        subm['r_'+str(f)] = rankdata(subm[str(f)])
subm['r_avg'] = subm[['r_'+f for f in models if f in subm.columns]].mean(axis=1)
subm['final_r_blend'] = MinMaxScaler().fit_transform(subm['r_avg'].reshape(-1, 1))
subm = subm[['name', 'final_r_blend']]
subm.columns = ['name', 'invasive']
subm.head()

In [ ]:
subm.to_csv(os.path.join(DATA_DIR, 'results', 'subm_jul_2_17_1.gz'), index=False, compression='gzip')

looks like some files had issues (some must have been a dif model somehow. (jun21). ok that wasnt that great. it only scored 0.98515

# summary

http://blog.kaggle.com/2017/04/20/dogs-vs-cats-redux-playground-competition-3rd-place-interview-marco-lugo/

https://gogul09.github.io/software/flower-recognition

good overview of voting/rank averraging ensembles:

http://andremeetsdata.com/2015/12/30/Numerai-Averaging

https://mlwave.com/kaggle-ensembling-guide/

https://www.kaggle.com/c/homesite-quote-conversion/discussion/18067

giving extra number after the decimal may hust us? worth investigating, or it could have no effect on receiver curve.

will try:

resnet: https://ctmakro.github.io/site/on_learning/resnet_keras.html

simplenet: https://arxiv.org/pdf/1608.06037.pdf

leaky relu: https://keras.io/layers/advanced-activations/

this site has desciptions for voting ensembles, cool: https://mlwave.com/kaggle-ensembling-guide/

in combinatio with my convolutional ensemble from before.